# Step 2: Normalize your data using sctransform

Use this notebook to normalize your data using the [sctransform](https://satijalab.org/seurat/articles/sctransform_vignette) package. 

Please note that the sctransform package is written in R. Therefore, in order to run this notebook you will first need to [install R]() on your system, as well as [sctransform version 0.4.1](https://github.com/satijalab/sctransform) and it's corresponding dependencies (including the optional dependency [glmGamPoi](https://github.com/const-ae/glmGamPoi)). 

Also note that your raw data input should be a csv file arranged using [tidy format](https://tidyr.tidyverse.org/articles/tidy-data.html). At a minimum your input csv should have five columns:
1. A column that corresponds to the first mode of your tensor. In metatranscriptomic data this column might indicate gene ID.
    - This first mode should generally be the longest in your tensor, and the one that corresponds to the variable you want clustered (e.g. genes in the case of metatranscriptomics data). The sparsity penalty (`lambda`) will be applied to this mode.
1. A column that corresponds to the second mode of your tensor. In metatranscriptomic data this column might indicate taxon ID.
1. A column that corresponds to the third mode of your tensor. This column should indicate sample ID.
    - **IMPORTANT: Sample IDs should be identical for different replicates of the same sample condition (see example below).**
1. A column that indicates the replicate ID of the sample.
1. A column that corresponds to the data variable. For raw metatranscriptomic data this column might contain read counts.

Here's a snippet of how an example csv might be arranged:

| gene_id | taxon_id   | sample_id | replicate | read_counts |
|---------|------------|-----------|-----------|-------------|
| K03839  | P. marinus | sample1   | A         | 3.02        |
| K03839  | P. marinus | sample1   | B         | 3.31        |
| K03839  | P. marinus | sample1   | C         | 3.18        |
| K03839  | P. marinus | sample2   | A         | 10.40       |
| ...     | ...        | ...       | ...       | ...         |
| K03320  | S. marinus | sample9   | C         | 0.05        |

In [29]:
# imports

# python packages
import math
import numpy as np
import os
import pandas as pd
import rpy2
import seaborn as sns

from matplotlib import pyplot as plt

# rpy2 imports
from rpy2 import robjects as ro
from rpy2.robjects.packages import importr
from rpy2.ipython.ggplot import image_png
from rpy2.robjects import pandas2ri
from rpy2.robjects.conversion import localconverter

# load rpy2 extension for ipython
%load_ext rpy2.ipython


The rpy2.ipython extension is already loaded. To reload it, use:
  %reload_ext rpy2.ipython


In [4]:
# Install required packages
%pip install rpy2

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Created wheel for rpy2-rinterface: filename=rpy2_rinterface-3.6.3-cp311-cp311-linux_x86_64.whl size=140348 sha256=71ecbf2f47de042f7e061a8fb06683cf6a5837fd7c1e69ae8f15abc29f5f22a0
  Stored in directory: /home/sr320/.cache/pip/wheels/9c/70/19/948292388eaaf757c279a12add5d0c5a886078cd51aa39a69f
Successfully built rpy2-rinterface
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4/4 [rpy2]2/4 [rpy2-robjects]e]
Note: you may need to restart the kernel to use updated packages.


In [30]:
# install & import sctransform and other r package dependencies

# check if sctransform is installed
if not ro.packages.isinstalled('sctransform'):
    # select CRAN mirror
    utils = importr('utils')
    utils.chooseCRANmirror(ind=1)
    # install sctransform
    utils.install_packages(ro.vectors.StrVector(['sctransform']))

# import sctransform and R Matrix package
sctransform = importr('sctransform')
rmatrix = importr('Matrix')

# check sctransform version (should be 0.4.1 or compatible)
print(f'Installed sctransform version: {sctransform.__version__}')
if not sctransform.__version__ in ['0.4.1', '0.4.2']:
    raise Exception('Please ensure that the installed sctransform is version 0.4.1 or 0.4.2')
    
# check that glmGamPoi dependency is installed
if not ro.packages.isinstalled('glmGamPoi'):
    print('Installing glmGamPoi dependency...')
    # install glmGamPoi from Bioconductor non-interactively
    utils = importr('utils')
    utils.install_packages(ro.vectors.StrVector(['BiocManager']))
    biocmanager = importr('BiocManager')
    biocmanager.install(ro.vectors.StrVector(['glmGamPoi']), ask=False, update=False)
    print('glmGamPoi installed successfully')


RNotReadyError: Embedded R is not ready to use.

In [23]:
# Fix Matrix package compatibility issue
try:
    # Try to fix the Matrix package compatibility issue
    utils = importr('utils')
    utils.install_packages("https://cran.r-project.org/src/contrib/Archive/Matrix/Matrix_1.5-3.tar.gz", repos=ro.NULL, type="source")
    rmatrix = importr('Matrix')
    print("Matrix package downgraded successfully")
except Exception as e:
    print(f"Could not downgrade Matrix package: {e}")
    print("Trying to continue with current version...")

R callback write-console: Installing package into ‘/home/sr320/R/x86_64-pc-linux-gnu-library/4.2’
(as ‘lib’ is unspecified)
  
R callback write-console: trying URL 'https://cran.r-project.org/src/contrib/Archive/Matrix/Matrix_1.5-3.tar.gz'
  
R callback write-console: Content type 'application/x-gzip'  
R callback write-console:  length 2163568 bytes (2.1 MB)
  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R cal

gcc -I"/opt/R/4.2.3/lib/R/include" -DNDEBUG -DNTIMER -I./SuiteSparse_config -DUSE_FC_LEN_T  -I/usr/local/include   -fpic  -g -O2  -c CHMfactor.c -o CHMfactor.o
gcc -I"/opt/R/4.2.3/lib/R/include" -DNDEBUG -DNTIMER -I./SuiteSparse_config -DUSE_FC_LEN_T  -I/usr/local/include   -fpic  -g -O2  -c Csparse.c -o Csparse.o
gcc -I"/opt/R/4.2.3/lib/R/include" -DNDEBUG -DNTIMER -I./SuiteSparse_config -DUSE_FC_LEN_T  -I/usr/local/include   -fpic  -g -O2  -c init.c -o init.o
gcc -I"/opt/R/4.2.3/lib/R/include" -DNDEBUG -DNTIMER -I./SuiteSparse_config -DUSE_FC_LEN_T  -I/usr/local/include   -fpic  -g -O2  -c Mutils.c -o Mutils.o
gcc -I"/opt/R/4.2.3/lib/R/include" -DNDEBUG -DNTIMER -I./SuiteSparse_config -DUSE_FC_LEN_T  -I/usr/local/include   -fpic  -g -O2  -c chm_common.c -o chm_common.o
gcc -I"/opt/R/4.2.3/lib/R/include" -DNDEBUG -DNTIMER -I./SuiteSparse_config -DUSE_FC_LEN_T  -I/usr/local/include   -fpic  -g -O2  -c cs.c -o cs.o
gcc -I"/opt/R/4.2.3/lib/R/include" -DNDEBUG -DNTIMER -I./SuiteSparse_con

ar: `u' modifier ignored since `D' is the default (see `U')


gcc -I"/opt/R/4.2.3/lib/R/include" -DNDEBUG -I../Include -I../../SuiteSparse_config  -I/usr/local/include   -fpic  -g -O2  -I../Include -DDLONG -c colamd.c -o colamd_l.o
ar -rucs ../../COLAMD.a colamd.o colamd_l.o
make[2]: Leaving directory '/tmp/RtmpYYRdq5/R.INSTALL3980a7413436a/Matrix/src/COLAMD/Source'
make[1]: Leaving directory '/tmp/RtmpYYRdq5/R.INSTALL3980a7413436a/Matrix/src/COLAMD'
make[1]: Entering directory '/tmp/RtmpYYRdq5/R.INSTALL3980a7413436a/Matrix/src/AMD'
( cd Source ; make -f "/opt/R/4.2.3/lib/R/etc/Makeconf" -f Makefile lib )
make[2]: Entering directory '/tmp/RtmpYYRdq5/R.INSTALL3980a7413436a/Matrix/src/AMD/Source'
gcc -I"/opt/R/4.2.3/lib/R/include" -DNDEBUG -I../Include -I../../SuiteSparse_config  -I/usr/local/include   -fpic  -g -O2  -I../Include -DDINT -c amd_aat.c -o amd_i_aat.o
gcc -I"/opt/R/4.2.3/lib/R/include" -DNDEBUG -I../Include -I../../SuiteSparse_config  -I/usr/local/include   -fpic  -g -O2  -I../Include -DDLONG -c amd_aat.c -o amd_l_aat.o
gcc -I"/opt/R/4

ar: `u' modifier ignored since `D' is the default (see `U')


...

make[1]: Leaving directory '/tmp/RtmpYYRdq5/R.INSTALL3980a7413436a/Matrix/src/SuiteSparse_config'
gcc -shared -L/opt/R/4.2.3/lib/R/lib -L/usr/local/lib -o Matrix.so CHMfactor.o Csparse.o init.o Mutils.o chm_common.o cs.o cs_utils.o dense.o dgCMatrix.o dgeMatrix.o dpoMatrix.o dppMatrix.o dsCMatrix.o dsyMatrix.o dspMatrix.o dtCMatrix.o dtrMatrix.o dtpMatrix.o factorizations.o sparseQR.o sparseVector.o abIndex.o packedMatrix.o unpackedMatrix.o sparse.o validity.o CHOLMOD.a COLAMD.a AMD.a SuiteSparse_config.a -llapack -lblas -lgfortran -lm -lquadmath -L/opt/R/4.2.3/lib/R/lib -lR


** R
** data
** inst
** byte-compile and prepare package for lazy loading


Creating a generic function for ‘zapsmall’ from package ‘base’ in package ‘Matrix’
Creating a generic function for ‘drop’ from package ‘base’ in package ‘Matrix’
Creating a generic function for ‘cov2cor’ from package ‘stats’ in package ‘Matrix’
Creating a generic function for ‘unname’ from package ‘base’ in package ‘Matrix’
in method for ‘coerce’ with signature ‘"matrix.csc","dgCMatrix"’: no definition for class “matrix.csc”
in method for ‘coerce’ with signature ‘"matrix.csr","dgRMatrix"’: no definition for class “matrix.csr”
in method for ‘coerce’ with signature ‘"matrix.coo","dgTMatrix"’: no definition for class “matrix.coo”
in method for ‘coerce’ with signature ‘"matrix.csr","dgCMatrix"’: no definition for class “matrix.csr”
in method for ‘coerce’ with signature ‘"matrix.coo","dgCMatrix"’: no definition for class “matrix.coo”
in method for ‘coerce’ with signature ‘"matrix.csc","CsparseMatrix"’: no definition for class “matrix.csc”
in method for ‘coerce’ with signature ‘"matrix.csc",

** help
*** installing help indices
** building package indices
** installing vignettes
** testing if installed package can be loaded from temporary location
** checking absolute paths in shared objects and dynamic libraries
** testing if installed package can be loaded from final location
** testing if installed package keeps a record of temporary installation path
* DONE (Matrix)


Matrix package downgraded successfully


In [26]:
# Install sctransform 0.4.1 specifically
try:
    utils = importr('utils')
    # Install specific version of sctransform
    utils.install_packages("https://cran.r-project.org/src/contrib/Archive/sctransform/sctransform_0.4.1.tar.gz", 
                          repos=ro.NULL, type="source")
    print("sctransform 0.4.1 installed successfully")
except Exception as e:
    print(f"Could not install sctransform 0.4.1: {e}")
    print("Continuing with current version...")

R callback write-console: Installing package into ‘/home/sr320/R/x86_64-pc-linux-gnu-library/4.2’
(as ‘lib’ is unspecified)
  
R callback write-console: trying URL 'https://cran.r-project.org/src/contrib/Archive/sctransform/sctransform_0.4.1.tar.gz'
  
R callback write-console: Content type 'application/x-gzip'  
R callback write-console:  length 197540 bytes (192 KB)
  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: =  
R callback write-console: 

g++ -std=gnu++17 -I"/opt/R/4.2.3/lib/R/include" -DNDEBUG  -I'/home/sr320/R/x86_64-pc-linux-gnu-library/4.2/RcppArmadillo/include' -I'/home/sr320/R/x86_64-pc-linux-gnu-library/4.2/Rcpp/include' -I/usr/local/include   -fpic  -g -O2  -c RcppExports.cpp -o RcppExports.o
g++ -std=gnu++17 -I"/opt/R/4.2.3/lib/R/include" -DNDEBUG  -I'/home/sr320/R/x86_64-pc-linux-gnu-library/4.2/RcppArmadillo/include' -I'/home/sr320/R/x86_64-pc-linux-gnu-library/4.2/Rcpp/include' -I/usr/local/include   -fpic  -g -O2  -c utils.cpp -o utils.o
g++ -std=gnu++17 -shared -L/opt/R/4.2.3/lib/R/lib -L/usr/local/lib -o sctransform.so RcppExports.o utils.o -llapack -lblas -lgfortran -lm -lquadmath -L/opt/R/4.2.3/lib/R/lib -lR


installing to /home/sr320/R/x86_64-pc-linux-gnu-library/4.2/00LOCK-sctransform/00new/sctransform/libs
** R
** data
*** moving datasets to lazyload DB
** inst
** byte-compile and prepare package for lazy loading
** help
*** installing help indices
** building package indices
** testing if installed package can be loaded from temporary location
** checking absolute paths in shared objects and dynamic libraries
** testing if installed package can be loaded from final location


sctransform 0.4.1 installed successfully


** testing if installed package keeps a record of temporary installation path
* DONE (sctransform)


In [31]:
# Restart R session and reload
import rpy2.rinterface as rinterface
# Restart the embedded R instance
%reload_ext rpy2.ipython

### Input data

In this step you will enter the variables necessary to:
1. Locate your input data
1. Configure your data tensor (i.e. which three variables correspond to the three different modes or axes)
1. Configure your normalization scheme

When it comes to normalization, there are several parameters you need to define:
- You will normalize by one of the variables that corresponds to a mode in your data tensor. You can think of this as the variable that defines the "within" groups. For example if I am normalizing by taxa, then the normalization procedure will be applied independently within each taxon in the dataset. Put another way, you can think of each taxon as a slab of your data tensor (i.e. a matrix), and the normalization will be applied independently to each slab.
- For each slab, you will define which of the remaining two modes best corresponds to samples, and which to genes. For example, in metatranscriptomic data annotated with KEGG orthologies, the sample ID would be the sample mode, and the KEGG ID would be the gene mode. Additionally, if you want to account for batch effects in your data, the batch variable should relate to your sample mode.
- You will define two thresholds that will apply to each slab (e.g. taxon):
    1. Sample threshold: each gene must be detected in at least this many samples. Genes that fall below the threshold will be removed. Default is 3.
    1. Detection threshold: each sample must contain non-zero values for at least this proportion of genes. Samples that fall below the threshold will be removed. Default is 0.01 (1%).
    - Note that data removed due to thresholding is preserved, saved, and displayed at the end of this notebook so it can be used for troubleshooting or to refine the thresholds and normalization work flow.
- If you want the normalization model to correct for batch effects, you will need to prepare a second csv file with columns corresponding to the sample mode in your data (including both sample ID and replicate), and with an additional column indicating the batch ID. For example, you might have a csv with the following headers: `['sample_id', 'replicate', 'batch_id']`. This file should include each unique combination of sample ID and replicate in your dataset, and the batch membership of each sample replicate should be indicated in the batch ID column.


In [20]:
# USER INPUTS -- edit these variables as needed

# data inputs
datapath = 'data/example-data.csv'  # Enter the filepath of your input data file
mode0 = 'KOfam'  # Enter the column name that will correspond to the first mode of your tensor
mode1 = 'phylum'  # Enter the column name that will correspond to the second mode of your tensor
mode2 = 'sample_name'  # Enter the column name that will correspond to the third mode of your tensor
rep = 'replicate'  # Enter the column name that corresponds to replicate IDs
data = 'counts'  # Enter the column name that corresponds to your data
outdir = 'data/barnacle/normalization'  # Enter the filepath of the output directory where you want files saved

# normalization parameters
norm_mode = 'phylum'  # Which mode do you want to normalize by? (enter name of mode)
sample_mode = 'sample_name'  # Which mode corresponds to your sample variable? (enter name of mode)
sample_thold = 3 # Each {gene_mode} must be detected in what minimum number of unique {sample_mode}s? (Default is 3)
gene_thold = 0.01 # Each {sample_mode} must contain what minimum proportion of nonzero {gene_mode}s? (Default is 0.01)
save_data = True  # Would you like to save the data output for each normalization? (Enter True/False)
save_plots = True  # Would you like to save the diagnostic plots for each normalization? (Enter True/False)
correction = False  # Would you like to correct for batch effects? (Enter True/False)
metadata_path = 'data/metadata.csv'  # Enter the filepath of your batch metadata file
batch_id = 'batch_id'  # Enter the column name that corresponds to the batch ID

# check output directory exists
if not os.path.exists(outdir):
    os.makedirs(outdir)

# check data file exists
if datapath and not os.path.isfile(datapath):
    raise Exception(f'Unable to find the file "{datapath}"')


In [21]:
# check the dataframes

# read in csv
df = pd.read_csv(datapath)

# check column names match inputs
for column in [mode0, mode1, mode2, rep, data]:
    if column not in df.columns:
        raise Exception(f'Column name "{column}" not found in headers of file {datapath}')

# define gene mode
gene_mode = [m for m in [mode0, mode1, mode2] if m not in [norm_mode, sample_mode]][0]

# tidy up dataframe
df = df[[mode0, mode1, mode2, rep, data]]

# make a unique identifier that combines sampleID and replicateID
df['sample_rep_id'] = df[sample_mode].astype(str) + '_' +  df[rep].astype(str)
display(df)

# read in metadata if using for batch correction
if correction:
    # check data file exists
    if not os.path.isfile(metadata_path):
        raise Exception(f'Unable to find the file "{metadata_path}"')
    # read in metadata file
    meta_df = pd.read_csv(metadata_path)
    # Batch id name cannot end in "y" or sctransform freaks out
    batch_id_new = batch_id[:-1] if batch_id[-1] == 'y' else batch_id
    meta_df[batch_id_new] = meta_df[batch_id]
    batch_id = batch_id_new
    
    # check for sample, replicate, and batch columns
    if sample_mode not in meta_df.columns:
        raise Exception(f'Column name "{sample_mode}" not found in headers of file {metadata_path}. Columns found: {meta_df.columns}')
    if rep not in meta_df.columns:
        raise Exception(f'Column name "{rep}" not found in headers of file {metadata_path}. Columns found: {meta_df.columns}')
    if not (meta_df[[sample_mode, rep]].drop_duplicates().reset_index(drop=True) == \
            df[[sample_mode, rep]].drop_duplicates().reset_index(drop=True)).all().all():
        raise Exception(f'Files {datapath} and {metadata_path} have different values for columns {sample_mode} and {rep}.')  
    if batch_id not in meta_df.columns:
        raise Exception(f'Column name "{batch_id}" not found in headers of file {metadata_path}. Columns found: {meta_df.columns}')

    # clean up metadata dataframe
    meta_df['sample_rep_id'] = meta_df[sample_mode].astype(str) + '_' + meta_df[rep].astype(str)
    meta_df = meta_df[['sample_rep_id', sample_mode, rep, batch_id]]
    display(meta_df)


KOfam           phylum      sample_name replicate      counts  \
0       K00002  Bacillariophyta  G3.UW.ALL.L25S1         A    21.00001   
1       K00003  Bacillariophyta  G3.UW.ALL.L25S1         A     0.00000   
2       K00006  Bacillariophyta  G3.UW.ALL.L25S1         A     3.00002   
3       K00010  Bacillariophyta  G3.UW.ALL.L25S1         A   161.58657   
4       K00011  Bacillariophyta  G3.UW.ALL.L25S1         A     3.00000   
...        ...              ...              ...       ...         ...   
961825  K26159    Pelagophyceae  G3.UW.ALL.L40S2         C     0.00000   
961826  K26163    Pelagophyceae  G3.UW.ALL.L40S2         C  1657.68445   
961827  K26165    Pelagophyceae  G3.UW.ALL.L40S2         C    23.19290   
961828  K26167    Pelagophyceae  G3.UW.ALL.L40S2         C    12.69730   
961829  K26171    Pelagophyceae  G3.UW.ALL.L40S2         C     3.00000   

            sample_rep_id  
0       G3.UW.ALL.L25S1_A  
1       G3.UW.ALL.L25S1_A  
2       G3.UW.ALL.L25S1_A  
3       G3.UW.ALL.L25S1_A  
4       G3.UW.ALL.L25S1_A  
...                   ...  
961825  G3.UW.ALL.L40S2_C  
961826  G3.UW.ALL.L40S2_C  
961827  G3.UW.ALL.L40S2_C  
961828  G3.UW.ALL.L40S2_C  
961829  G3.UW.ALL.L40S2_C  

[961830 rows x 6 columns]

### Run sctransform on each slab of data

In this step you'll run the sctransform model on your data. If you selected it in the first step, the data and/or plots resulting from each normalization run will be saved to the designated output directory.

In [17]:
# helper functions for running normalization model

# function to threshold sparsity of pandas dataframes
def sparsity_thold_df(df, thold, axis=0):
    """Apply a sparsity threshold to a pandas.DataFrame so that only columns or rows with 
    greater than or equal to the threshold amount of nonzero values are retained.
    
    Parameters
    ----------
    df : pandas.DataFrame
        Input dataframe object.
    thold : {int, float}
        Threshold. If parameter is an int, then retained vectors must contain at least that number of 
        nonzero values. If parameter is a float, then at least this proportion of the vector must be nonzero.
    axis : int
        Axis to which threshold is applied. 
            
    Returns
    -------
    df : pandas.DataFrame
        Thresholded dataframe.
    dropped_data_df : pandas.DataFrame
        Data removed from the input dataframe as a result of the threshold
    """
    if type(thold) is float:
        thold = math.ceil(df.shape[axis] * thold)
    elif type(thold) is not int:
        raise Exception('Parameter `thold` must be either an int or float type value.')
    mask = (df != 0).sum(axis).ge(thold)
    if axis == 0:
        output_df = df.loc[:, mask]
        dropped_df = df.loc[:, ~mask]
    elif axis == 1:
        output_df = df.loc[mask, :]
        dropped_df = df.loc[~mask, :]
    else:
        raise Exception('Invalid value for `axis` parameter.')
    return output_df, dropped_df


# function to calculate 0-sensitive geometric mean
def geometric_mean(vector, pseudocount=1):
    return np.exp(np.mean(np.log(vector + pseudocount))) - pseudocount


# function to convert pandas dataframe to r matrix
def pandas_dataframe_to_r_matrix(df, dtype=float):
    """
    Function to convert pandas DataFrame objects to R matrix objects.
    """
    if dtype is float:
        vector = ro.vectors.FloatVector(df.values.flatten().tolist())
    elif dtype is str:
        vector = ro.vectors.StrVector(df.values.flatten().tolist())
    elif dtype is int:
        vector = ro.vectors.FloatVector(df.values.flatten().tolist())
    else:
        raise ValueError('The dtype {} is not recognized'.format(dtype))
    matrix = rmatrix.Matrix(
        data=vector, 
        nrow=df.shape[0], 
        ncol=df.shape[1], 
        byrow=True, 
        dimnames=[df.index.to_list(), df.columns.to_list()], 
        sparse=True
    )
    return matrix
    

In [25]:
# run the model on each slab

# initialize residuals dataframe
residuals_df = pd.DataFrame()

# keep track of filtered data
dropped_data_df = pd.DataFrame()

# iterate through slabs
slab_ids = df[norm_mode].unique()
for i, slab_id in enumerate(slab_ids):
    # separate out data
    slab_df = df[df[norm_mode].eq(slab_id)].pivot(index=gene_mode, columns=['sample_rep_id'], values=data).fillna(0)
    # apply sample threshold to filter out low-prevalence genes
    slab_df, drop_df = sparsity_thold_df(slab_df, sample_thold, axis=1)
    drop_df = drop_df.melt(value_name=data, ignore_index=False).reset_index()
    drop_df[norm_mode] = slab_id
    drop_df['drop_reason'] = f'{gene_mode} detected in fewer than {sample_thold} {sample_mode}s'
    dropped_data_df = pd.concat([dropped_data_df, drop_df])
    # apply gene threshold to filter out samples with low detection
    slab_df, drop_df = sparsity_thold_df(slab_df, gene_thold, axis=0)
    drop_df = drop_df.melt(value_name=data, ignore_index=False).reset_index()
    drop_df[norm_mode] = slab_id
    drop_df['drop_reason'] = f'{sample_mode} contains fewer than {math.ceil(slab_df.shape[0] * gene_thold)} nonzero {gene_mode}s'
    dropped_data_df = pd.concat([dropped_data_df, drop_df])
    # check for very small slabs
    if (slab_df.shape[0] < 10) or (slab_df.shape[1] < sample_thold):
        print(f'Skipping slab {i+1} of {len(slab_ids)}: {slab_id} ({slab_df.shape[1]} samples, {slab_df.shape[0]} genes)', flush=True)
        print('\tLimited nonzero data in this slab undermines the reliability of normalization with sctransform.', flush=True)
        drop_df = slab_df.melt(value_name=data, ignore_index=False).reset_index()
        drop_df[norm_mode] = slab_id
        drop_df['drop_reason'] = f'{norm_mode} encompassed fewer than 10 {gene_mode}s or fewer than {sample_thold} {sample_mode}s'
        dropped_data_df = pd.concat([dropped_data_df, drop_df])
        continue
    else:
        print(f'Normalizing slab {i+1} of {len(slab_ids)}: {slab_id} ({slab_df.shape[1]} samples, {slab_df.shape[0]} genes)', flush=True)

    # make r version of slab dataframe
    r_slab_df = pandas_dataframe_to_r_matrix(slab_df)
    # pull out batch information
    if correction:
        sample_attr_df = meta_df.set_index('sample_rep_id').loc[slab_df.columns, [sample_mode, rep, batch_id]]
        with localconverter(ro.default_converter + pandas2ri.converter):
            r_sample_attr_df = ro.conversion.py2rpy(sample_attr_df)

    # fit vst normalization model
    if correction:
        result = sctransform.vst(
            r_slab_df, cell_attr=r_sample_attr_df, batch_var=ro.vectors.StrVector([batch_id]), 
            min_cells=sample_thold, vst_flavor='v2', verbosity=2
        )
    else:
        result = sctransform.vst(
            r_slab_df, min_cells=sample_thold, vst_flavor='v2', verbosity=2
        )

    # convert residuals result to a dataframe
    result_df = pd.DataFrame(
        np.asarray(result[0]), 
        index=slab_df.index, 
        columns=slab_df.columns
    )

    # prepare to save requested outputs
    if save_data or save_plots:
        # make unique output directory per slab
        dir_path = f'{outdir}/{slab_id}'
        if not os.path.isdir(dir_path):
            os.makedirs(dir_path)
        # calculate residuals
        residual_var = result_df.var(axis=1)

    # save data if requested
    if save_data:
        # save csv of residuals
        result_df.to_csv(f'{dir_path}/residuals_{slab_id}.csv')
        # save csv of residual variances
        res_var_df = residual_var.reset_index().rename(columns={0:'residual_variance'})
        res_var_df = res_var_df.sort_values('residual_variance', ascending=False).reset_index()
        res_var_df.to_csv(f'{dir_path}/residual_variances_{slab_id}.csv')

    # save plots if requested
    if save_plots:
        # plots of model parameters
        plots = sctransform.plot_model_pars(result, show_theta=True)
        img = image_png(plots)
        with open(f'{dir_path}/parameters_{slab_id}.png', 'wb') as png:
            png.write(img.data)
        # plot of high variance genes
        means = slab_df.apply(geometric_mean, axis=1)
        plt.figure(figsize=(10, 4))
        sns.scatterplot(x=means, y=residual_var, alpha=0.1);
        plt.xlabel(f'geometric mean of {gene_mode} {data}')
        plt.xscale('log')
        plt.ylabel('residual variance')
        plt.title(f'normalized residual variance\nvs. mean {gene_mode} {data} ({slab_id})')
        plt.savefig(f'{dir_path}/residual_variances_{slab_id}.png')
        plt.show()

    # concatenate result with other residuals
    result_df = result_df.melt(value_name='residual', ignore_index=False).reset_index()
    result_df[norm_mode] = slab_id
    residuals_df = pd.concat([residuals_df, result_df])
        

Normalizing slab 1 of 8: Bacillariophyta (28 samples, 7076 genes)


R callback write-console: vst.flavor='v2' set. Using model with fixed slope and excluding poisson genes.
  
R callback write-console: Calculating cell attributes from input UMI matrix: log_umi
  
R callback write-console: Total Step 1 genes: 7076
  
R callback write-console: Total overdispersed genes: 7075
  
R callback write-console: Excluding 1 genes from Step 1 because they are not overdispersed.
  
R callback write-console: Calculating cell attributes from input UMI matrix: log_umi
  
R callback write-console: Total Step 1 genes: 7076
  
R callback write-console: Total overdispersed genes: 7075
  
R callback write-console: Excluding 1 genes from Step 1 because they are not overdispersed.
  
R callback write-console: Variance stabilizing transformation of count matrix of size 7076 by 28
  
R callback write-console: Model formula is y ~ log_umi
  
R callback write-console: Get Negative Binomial regression parameters per gene
  
R callback write-console: Using 2000 genes, 28 cells
  


  |                                                                      |   0%

R callback write-console: Error in rowAnys(x, rows, cols, value = NA, ..., useNames = useNames) : 
  Argument 'useNames' must be either TRUE or FALSE
  


RRuntimeError: Error in rowAnys(x, rows, cols, value = NA, ..., useNames = useNames) : 
  Argument 'useNames' must be either TRUE or FALSE


In [7]:
# save normalized data as a csv

# add back sample information
residuals_df = pd.merge(residuals_df, df[['sample_rep_id', sample_mode, rep]].drop_duplicates(), on='sample_rep_id', how='left')

# add in raw count data
residuals_df = pd.merge(residuals_df, df, on=['sample_rep_id', mode0, mode1, mode2, rep], how='left').fillna(0)

# tidy up dataframe
residuals_df = residuals_df[[mode0, mode1, mode2, rep, data, 'residual']]

# save output
residuals_df.to_csv(f'{outdir}/normalized-residuals.csv')

residuals_df


KOfam           phylum      sample_name replicate      counts  \
0        K00001  Bacillariophyta  G3.UW.ALL.L25S1         A     0.00000   
1        K00002  Bacillariophyta  G3.UW.ALL.L25S1         A    21.00001   
2        K00003  Bacillariophyta  G3.UW.ALL.L25S1         A     0.00000   
3        K00004  Bacillariophyta  G3.UW.ALL.L25S1         A     0.00000   
4        K00006  Bacillariophyta  G3.UW.ALL.L25S1         A     3.00002   
...         ...              ...              ...       ...         ...   
1284467  K26159    Pelagophyceae  G3.UW.ALL.L40S2         C     0.00000   
1284468  K26163    Pelagophyceae  G3.UW.ALL.L40S2         C  1657.68445   
1284469  K26165    Pelagophyceae  G3.UW.ALL.L40S2         C    23.19290   
1284470  K26167    Pelagophyceae  G3.UW.ALL.L40S2         C    12.69730   
1284471  K26171    Pelagophyceae  G3.UW.ALL.L40S2         C     3.00000   

             residual  
0       -9.222961e-13  
1        2.092099e+00  
2       -1.128763e+00  
3       -1.635693e-02  
4       -6.474356e-01  
...               ...  
1284467 -1.360729e-01  
1284468  1.537219e+00  
1284469  6.104757e-01  
1284470  8.077639e-01  
1284471 -3.022025e-01  

[1284472 rows x 6 columns]

In [8]:
# examine data that was removed during normalization process

# remove zero values
dropped_data_df = dropped_data_df[dropped_data_df[data] != 0.0]

# add back sample information
dropped_data_df = pd.merge(dropped_data_df, df[['sample_rep_id', sample_mode, rep]].drop_duplicates(), on='sample_rep_id', how='left')

# tidy up dataframe
dropped_data_df = dropped_data_df[[mode0, mode1, mode2, rep, data, 'drop_reason']]

# show some summary statistics
for variable in ['drop_reason', mode0, mode1, mode2]:
    print(dropped_data_df[variable].value_counts())

# save drop data
dropped_data_df.to_csv(f'{outdir}/removed-data.csv')      

dropped_data_df


drop_reason
KOfam detected in fewer than 3 sample_names    3017
Name: count, dtype: int64
KOfam
K00015    6
K25390    5
K15462    5
K16422    5
K10638    4
         ..
K19222    1
K22089    1
K01368    1
K03025    1
K17064    1
Name: count, Length: 1757, dtype: int64
phylum
Haptophyta          494
Bacillariophyta     436
Pelagophyceae       428
Dictyochophyceae    414
Chlorophyta         383
Bolidophyceae       312
Chrysophyceae       309
Ciliophora          241
Name: count, dtype: int64
sample_name
G3.UW.ALL.L40S1    962
G3.UW.ALL.L40S2    321
G3.UW.ALL.L37S1    273
G3.UW.ALL.L35S1    270
G3.UW.ALL.L38S1    250
G3.UW.ALL.L35S2    199
G3.UW.ALL.L32S3    168
G3.UW.ALL.L25S1    159
G3.UW.ALL.L32S1    152
G3.UW.ALL.L29S1    139
G3.UW.ALL.L31S2    124
Name: count, dtype: int64


KOfam           phylum      sample_name replicate    counts  \
0     K04261  Bacillariophyta  G3.UW.ALL.L25S1         A   2.00000   
1     K10720  Bacillariophyta  G3.UW.ALL.L25S1         A   1.00000   
2     K17353  Bacillariophyta  G3.UW.ALL.L25S1         A   6.35636   
3     K20847  Bacillariophyta  G3.UW.ALL.L25S1         A   1.00000   
4     K22619  Bacillariophyta  G3.UW.ALL.L25S1         A   4.74145   
...      ...              ...              ...       ...       ...   
3012  K16197    Pelagophyceae  G3.UW.ALL.L40S2         C   4.00000   
3013  K16581    Pelagophyceae  G3.UW.ALL.L40S2         C  10.95080   
3014  K16634    Pelagophyceae  G3.UW.ALL.L40S2         C   6.00000   
3015  K17064    Pelagophyceae  G3.UW.ALL.L40S2         C   1.33754   
3016  K22679    Pelagophyceae  G3.UW.ALL.L40S2         C   5.06391   

                                      drop_reason  
0     KOfam detected in fewer than 3 sample_names  
1     KOfam detected in fewer than 3 sample_names  
2     KOfam detected in fewer than 3 sample_names  
3     KOfam detected in fewer than 3 sample_names  
4     KOfam detected in fewer than 3 sample_names  
...                                           ...  
3012  KOfam detected in fewer than 3 sample_names  
3013  KOfam detected in fewer than 3 sample_names  
3014  KOfam detected in fewer than 3 sample_names  
3015  KOfam detected in fewer than 3 sample_names  
3016  KOfam detected in fewer than 3 sample_names  

[3017 rows x 6 columns]